# The main goal of my project is to be able to identify where a set of 3 images (one location with 3 screenshots) was taken using data from Google Maps. This dataset only uses locations from Europe

## Import Functions

In [1]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
%matplotlib inline
import os
import geopandas as gpd
from shapely.geometry import Point
import seaborn as sns
from sklearn.metrics import accuracy_score
from scipy import linalg
from matplotlib.image import imread
from skimage.transform import resize
import time

In [2]:
from sklearn.model_selection import train_test_split,learning_curve
from sklearn import datasets, metrics, svm 
from sklearn import metrics
from sklearn.neighbors import NearestNeighbors
from tensorflow.keras import layers, models
from tensorflow.keras.utils import to_categorical
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.datasets import make_classification
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay

# Accessing all of the data and then creating a data frame to access the data

In [3]:
file_dir = 'images/' #accesing the dataset 
cords = os.listdir(file_dir)
cords = cords[1:17601]

In [4]:
lat_list = np.zeros(len(cords)) #creating a df of the latitude/longitude and region of each locaton
long_list = np.zeros(len(cords))
country_region = np.zeros(len(cords))

for i in range(len(cords)):
    country,long,lat = cords[i].split(",")
    country_region[i] = country
    long_list[i] = long
    lat_list[i] = lat
    
europe = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres')) #using geopandas to find the country each location is in based on lat/long
europe = europe[europe['continent'] == 'Europe']
def get_country(lat,long):
    point = Point(lat,long)
    for idx, country in europe.iterrows():
        if country['geometry'].contains(point):
            return country['name']
country_list = []
for i in range(len(cords)):
    country_list.append(get_country(lat_list[i],long_list[i]))
countries_keep = ['Austria','Belgium', 'Bosnia and Herz.','Croatia','Czechia','France','Hungary','Italy','Netherlands','Poland','Portugal','Spain', 'Slovakia', 'Slovenia','Switzerland']
index_keep = []
#removes all of the excess countries, there are some countries that are outside of the 15 countries I'm predicting becuase when
#I found the country names I used a lowres image. This also creates error in my model
for i in range(len(cords)):
    if country_list[i] in countries_keep:
        index_keep.append(country_list[i])

column_names = ['latitude','longitude','country_name','country_region']
df = pd.DataFrame(columns = column_names)
for i in range(len(cords)):
    if country_list[i] in countries_keep:
        new_row = {'latitude':pd.to_numeric(lat_list[i], errors='coerce'),'longitude':pd.to_numeric(long_list[i], errors='coerce'), 'country_name':country_list[i],'country_region':country_region[i]}
        df = df.append(new_row,ignore_index= True)

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:11: FutureWarning: The geopandas.dataset module is deprecated and will be removed in GeoPandas 1.0. You can get the original 'naturalearth_lowres' data from https://www.naturalearthdata.com/downloads/110m-cultural-vectors/.
  europe = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres')) #using geopandas to find the country each location is in based on lat/long
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning:

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

...

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\Local\Temp\ipykernel_8348\784137700.py:34: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row,ignore_index= True)
C:\Users\Lucas\AppData\L

#### My dataset is so big that I have to use a smaller sample, so 1) this can run properly for the project and 2) my laptop doesn't crash

In [5]:
df = df.sample(frac = 1,random_state = 42) #shuffles the data set 
df_set = df
df = df[:3000] #takes the first 3000 images in the shuffled data set
df
y = df['country_region']

# Using linear algebra to reduce size of images for quicker models

### Typically in a standard dataset there would be significantly more data cleaning, however due to the constraints of my dataset only being images and locations and the time given for this project in the class this is the only "data cleaning" 

In [6]:
def image_size_creater(img_size):
    start_time = time.time()
    X = []
    for i in range(df.shape[0]):
        folder_path = f'images/{int(df["country_region"].iloc[i])},{df["longitude"].iloc[i]},{df["latitude"].iloc[i]}'
        file_list = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

        image_a = imread(folder_path+f'/{file_list[0]}')
        image_a_res = resize(image_a,(img_size,img_size))
        image_a_bnw = np.mean(image_a_res,-1)
        U,S,V_T = linalg.svd(image_a_bnw)  
        imga = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]


        image_b = imread(folder_path+f'/{file_list[1]}')
        image_b_res = resize(image_b,(img_size,img_size))
        image_b_bnw = np.mean(image_b_res,-1) 

        U,S,V_T = linalg.svd(image_b_bnw)  
        imgb = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]

        image_c = imread(folder_path+f'/{file_list[2]}')
        image_c_res = resize(image_c,(img_size,img_size))
        image_c_bnw = np.mean(image_c_res,-1)

        U,S,V_T = linalg.svd(image_c_bnw)  
        imgc = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]

        img_combined = np.concatenate([imga,imgb,imgc],axis=0) #puts all the images into one variable (stacks them together)
        
        img1d = img_combined.flatten() #converts image into 1d ary so it can be used by ML model
        X.append(img1d) #puts all images into a list
    
    print('image size',img_size,'time taken to create',time.time()-start_time)
    return X

In [8]:
X_75 = image_size_creater(75) 

image size 75 time taken to create 242.0818817615509


# Testing out different models to see which one works best 

### SVM (Support Vector Machines):  I'm testing out SVM models due to their ability to work with multiclass classification which will be useful in identifying similar objects (such as styles of electrical posts, signs, flags). A con with these types of models are that they are slower for larger data sets such as the one I am using. 

In [9]:
y = df['country_region']
X_train, X_test, y_train, y_test = train_test_split(X_75,y,test_size = .4,random_state=42)

svm_model = svm.SVC(kernel ='linear')
svm_model.fit(X_train,y_train)

y_pred= svm_model.predict(X_test)

acc = accuracy_score(y_test,y_pred)
print(acc)

0.020833333333333332


### That's a horrendous accuracy score which is to be expected with a linear kernel type and my dataset. So I'm going to test out some different hyperparmeters to see if there might be anything that could be a bit better. I'm trying out a hyperparameter grid so I don't have to check multiple myself (and save myself some lines of code) 

In [10]:
param_grid = {'C': [0.1, 1, 10, 100], 'kernel': ['rbf', 'poly','sigmoid']}

svm_model = svm.SVC()

grid_search = GridSearchCV(svm_model, param_grid, cv=5)
grid_search.fit(X_train, y_train)

best_params = grid_search.best_params_
print(f"Best Hyperparameters: {best_params}")

best_model = grid_search.best_estimator_
y_pred = best_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Test Accuracy with Best Hyperparameters: {accuracy}")

Best Hyperparameters: {'C': 1, 'kernel': 'rbf'}
Test Accuracy with Best Hyperparameters: 0.03


### After running this my accuracy didn't really improve so I'm going to see what other models could work better. But it is good to note that the best current hyperparameters are C: 1 and rbf kernel type. 

### Random Forest Classifier: I'm testing a Random Forest Classifier Model due to its ability in handing high dimensional data and multiple features (Vegatation of areas, language of signs dectected, which side of the road the car is on, etc). Cons of using Random forest Classifier is the computational resources that it requires. This makes it difficult to do some hyperparameter tuning (especially with a laptop with no GPU such as my own) 

In [32]:
from sklearn.ensemble import RandomForestClassifier

rf_classifier = RandomForestClassifier(n_estimators=100, random_state=42)

rf_classifier.fit(X_train, y_train)


y_pred = rf_classifier.predict(X_test)


acc = accuracy_score(y_test, y_pred)
print(acc)

0.03


In [34]:
param_grid = {
    'n_estimators': [50, 100, 150],  # Adding more options for number of estimators
    'max_depth': [10, 20, 30],        # Increasing the maximum depth options
    'min_samples_split': [2, 5, 10],  # Adding more options for min_samples_split
    'min_samples_leaf': [1, 2, 4]     # Adding more options for min_samples_leaf
}


# Initialize Random Forest Classifier
rf_classifier = RandomForestClassifier(random_state=42)

# Perform Grid Search with cross-validation
grid_search = GridSearchCV(rf_classifier, param_grid, cv=5)
grid_search.fit(X_train, y_train)

best_params = grid_search.best_params_
print(f"Best Hyperparameters: {best_params}")

# Evaluate model with best hyperparameters on test set
best_model = grid_search.best_estimator_
y_pred = best_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Test Accuracy with Best Hyperparameters: {accuracy}")


Best Hyperparameters: {'max_depth': 20, 'min_samples_leaf': 2, 'min_samples_split': 5, 'n_estimators': 100}
Test Accuracy with Best Hyperparameters: 0.021666666666666667


### I spent a lot of time for nothing, thats pretty cool

In [13]:
rf_classifier = RandomForestClassifier(n_estimators=100,max_depth = None,min_samples_split = 2, random_state=42)

rf_classifier.fit(X_train, y_train)


y_pred = rf_classifier.predict(X_test)


acc = accuracy_score(y_test, y_pred)
print(acc)

0.03


### K-Nearest Neighbors:

In [14]:
knn_classifier = KNeighborsClassifier(n_neighbors=3)  # You can adjust the number of neighbors (k) as needed

# Train the classifier
knn_classifier.fit(X_train, y_train)

# Make predictions
y_pred = knn_classifier.predict(X_test)

# Evaluate accuracy
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy: {accuracy}")

Accuracy: 0.0125


C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [15]:
knn_classifier = KNeighborsClassifier()

# Define the parameter grid
param_grid = {
    'n_neighbors': [3, 5, 7, 9],
    'weights': ['uniform', 'distance'],
    'metric': ['euclidean', 'manhattan']
}

# Perform Grid Search with cross-validation
grid_search = GridSearchCV(knn_classifier, param_grid, cv=5)
grid_search.fit(X_train, y_train)

# Get the best hyperparameters
best_params = grid_search.best_params_
print(f"Best Hyperparameters: {best_params}")

# Evaluate model with best hyperparameters on test set
best_model = grid_search.best_estimator_
y_pred = best_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Test Accuracy with Best Hyperparameters: {accuracy}")

C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)
C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set 

C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)
C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set 

C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)
C:\Users\Lucas\anacond_fresh\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set 

Best Hyperparameters: {'metric': 'euclidean', 'n_neighbors': 7, 'weights': 'distance'}
Test Accuracy with Best Hyperparameters: 0.010833333333333334


### Convolution Neural Networks: 

In [5]:
import tensorflow as tf

In [31]:
np.random.seed(42)
tf.random.set_seed(42)
model = tf.keras.Sequential([
    tf.keras.layers.Flatten(input_shape=[16875], dtype=tf.uint8),
    tf.keras.layers.Rescaling(scale=1 / 255),
    tf.keras.layers.Dense(1000, activation="relu"),
    tf.keras.layers.Dense(1000, activation="relu"),
    tf.keras.layers.Dense(88, activation="softmax")
])
model.compile(loss="sparse_categorical_crossentropy",
              optimizer=tf.keras.optimizers.SGD(learning_rate=1e-2),
              metrics=["accuracy"])
y_train_stacked = tf.stack(y_train)
X_train_stacked = tf.stack(X_train)
X_test_stacked = tf.stack(X_test)
y_test_stacked = tf.stack(y_test)
history = model.fit(X_train_stacked, y_train_stacked, epochs=10,
                    validation_data=(X_test_stacked, y_test_stacked))

Epoch 1/10
57/57 [==============================] - 6s 107ms/step - loss: 4.4773 - accuracy: 0.0106 - val_loss: 4.4772 - val_accuracy: 0.0133
Epoch 2/10
57/57 [==============================] - 6s 100ms/step - loss: 4.4765 - accuracy: 0.0178 - val_loss: 4.4771 - val_accuracy: 0.0142
Epoch 3/10
57/57 [==============================] - 6s 102ms/step - loss: 4.4758 - accuracy: 0.0144 - val_loss: 4.4770 - val_accuracy: 0.0142
Epoch 4/10
57/57 [==============================] - 6s 102ms/step - loss: 4.4751 - accuracy: 0.0150 - val_loss: 4.4769 - val_accuracy: 0.0142
Epoch 5/10
57/57 [==============================] - 6s 101ms/step - loss: 4.4744 - accuracy: 0.0144 - val_loss: 4.4768 - val_accuracy: 0.0142
Epoch 6/10
57/57 [==============================] - 6s 104ms/step - loss: 4.4736 - accuracy: 0.0172 - val_loss: 4.4767 - val_accuracy: 0.0142
Epoch 7/10
57/57 [==============================] - 6s 100ms/step - loss: 4.4730 - accuracy: 0.0150 - val_loss: 4.4767 - val_accuracy: 0.0142
Epoch 

# All of my options are looking pretty tough. I'm going to hone in on RandomForestClassifer due to how accurate the initial model was. I'm also going to explore a little bit more with some tensorflow models.

## Due to how inaccurate my models are. I'm going to try and play around with some of my data image sizes and set sizes to see if that can make it a little more accurate

In [ ]:
df = df_set [:6000]
X_150 = image_size_creater(150)

y = df['country_region']
X_train, X_test, y_train, y_test = train_test_split(X_150,y,test_size = .4,random_state=42)

In [38]:
rf_classifier = RandomForestClassifier(n_estimators=100, random_state=42)

rf_classifier.fit(X_train, y_train)


y_pred = rf_classifier.predict(X_test)


acc = accuracy_score(y_test, y_pred)
print(acc)

0.028333333333333332


In [39]:
param_grid = {
    'n_estimators': [50, 100, 150],  # Adding more options for number of estimators
    'max_depth': [10, 20, 30],        # Increasing the maximum depth options
    'min_samples_split': [2, 5, 10],  # Adding more options for min_samples_split
    'min_samples_leaf': [1, 2, 4]     # Adding more options for min_samples_leaf
}


# Initialize Random Forest Classifier
rf_classifier = RandomForestClassifier(random_state=42)

# Perform Grid Search with cross-validation
grid_search = GridSearchCV(rf_classifier, param_grid, cv=5)
grid_search.fit(X_train, y_train)

best_params = grid_search.best_params_
print(f"Best Hyperparameters: {best_params}")

# Evaluate model with best hyperparameters on test set
best_model = grid_search.best_estimator_
y_pred = best_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Test Accuracy with Best Hyperparameters: {accuracy}")

Best Hyperparameters: {'max_depth': 30, 'min_samples_leaf': 4, 'min_samples_split': 2, 'n_estimators': 150}
Test Accuracy with Best Hyperparameters: 0.030416666666666668


In [42]:
rf_classifier = RandomForestClassifier(n_estimators=150,max_depth= 30,min_samples_leaf = 4, min_samples_split=2, random_state=42)

rf_classifier.fit(X_train, y_train)


y_pred = rf_classifier.predict(X_test)


acc = accuracy_score(y_test, y_pred)
print(acc)

0.030416666666666668


### Since nothing is working from class, I've decieded to use information from an unused chapter (ch 11) in our class to try and get a better accuracy score 

In [6]:
import random

In [7]:
shuffled_df = df.sample(frac=1).reset_index(drop=True)

In [8]:
df = shuffled_df[:3000]

In [9]:
def image_size_creator(img_size):
    start_time = time.time()
    X = []
    
    # Assuming df and other variables are defined elsewhere
    
    for i in range(df.shape[0]):
        folder_path = f'images/{int(df["country_region"].iloc[0])},{df["longitude"].iloc[0]},{df["latitude"].iloc[0]}'
        file_list = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

        # Assuming df and other variables are defined elsewhere
        image_a = imread(folder_path+f'/{file_list[0]}')
        image_a_res = resize(image_a,(img_size,img_size))
        image_a_bnw = np.mean(image_a_res,-1)
        U,S,V_T = linalg.svd(image_a_bnw)  
        imga = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]


        image_b = imread(folder_path+f'/{file_list[1]}')
        image_b_res = resize(image_b,(img_size,img_size))
        image_b_bnw = np.mean(image_b_res,-1) 

        U,S,V_T = linalg.svd(image_b_bnw)  
        imgb = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]

        image_c = imread(folder_path+f'/{file_list[2]}')
        image_c_res = resize(image_c,(img_size,img_size))
        image_c_bnw = np.mean(image_c_res,-1)

        U,S,V_T = linalg.svd(image_c_bnw)  
        imgc = U[:,:25] @ np.diag(S[:25]) @ V_T[:25,:]

        img_combined = [image_a_res,image_b_res,image_c_res]
        img_stacked = np.stack(img_combined,axis=0)
        img_con = np.concatenate(img_stacked,axis=-1)
        final_img = img_con.reshape((224,224,-1))[:,:,:3]

        X.append(final_img)
    
    print('Image size', img_size, 'Time taken to create', time.time() - start_time)
    return X

In [10]:
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.resnet50 import preprocess_input, decode_predictions

In [11]:
X_224 = image_size_creator(224)

Image size 224 Time taken to create 742.7922501564026


In [13]:
y = df['country_region']
X_train, X_test, y_train, y_test = train_test_split(X_224,y,test_size = .4,random_state=42)

In [14]:
y_train_stacked = tf.stack(y_train)
X_train_stacked = tf.stack(X_train)
X_test_stacked = tf.stack(X_test)
y_test_stacked = tf.stack(y_test)

In [23]:
y_train = to_categorical(y_train_stacked, 88)
y_test = to_categorical(y_test_stacked, 88)

In [16]:
tensor_shape = tf.shape(X_train_stacked)
batch_size = tensor_shape[0]
height = tensor_shape[1]
width = tensor_shape[2]
channels = tensor_shape[3]
flattened_tensor = tf.reshape(X_train_stacked, [batch_size, height, width ,channels])


In [31]:
base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))



# Add custom layers on top of the base model
inputs = tf.keras.Input(shape=(224, 224, 3))
x = base_model(inputs)
x = layers.GlobalAveragePooling2D()(x)  # Global average pooling layer
x = layers.Dense(128, activation='relu')(x)  # Custom Dense layer
outputs = layers.Dense(88, activation='softmax')(x)  # Adjust num_classes for your task

# Create the combined model
model = tf.keras.Model(inputs, outputs)
for layer in model.layers[:-5]:
    layer.trainable = False
# Compile the model
model = models.Sequential([
    layers.Conv2D(32, (3, 3), activation='relu', input_shape=(224, 224, 3)),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(128, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(128, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.Flatten(),
    layers.Dropout(0.5),  # Dropout layer with 50% dropout rate
    layers.Dense(64, activation='relu'),
    layers.Dense(88, activation='softmax')
])

model.compile(optimizer='adam',
              loss='categorical_crossentropy',
              metrics=['accuracy'])

# Assuming flattened_tensor is your input data and y_train is your one-hot encoded labels
model.fit(flattened_tensor, y_train, epochs=15, batch_size=32, validation_split=0.2)


Epoch 1/15
45/45 [==============================] - 168s 4s/step - loss: 16.9613 - accuracy: 0.0056 - val_loss: 4.4770 - val_accuracy: 0.0250
Epoch 2/15
45/45 [==============================] - 166s 4s/step - loss: 4.4759 - accuracy: 0.0111 - val_loss: 4.4764 - val_accuracy: 0.0111
Epoch 3/15
45/45 [==============================] - 167s 4s/step - loss: 4.4745 - accuracy: 0.0181 - val_loss: 4.4758 - val_accuracy: 0.0111
Epoch 4/15
45/45 [==============================] - 176s 4s/step - loss: 4.4731 - accuracy: 0.0139 - val_loss: 4.4751 - val_accuracy: 0.0111
Epoch 5/15
45/45 [==============================] - 175s 4s/step - loss: 4.4719 - accuracy: 0.0181 - val_loss: 4.4747 - val_accuracy: 0.0111
Epoch 6/15
45/45 [==============================] - 198s 4s/step - loss: 4.4707 - accuracy: 0.0139 - val_loss: 4.4740 - val_accuracy: 0.0111
Epoch 7/15
45/45 [==============================] - 150s 3s/step - loss: 4.4695 - accuracy: 0.0181 - val_loss: 4.4739 - val_accuracy: 0.0111
Epoch 8/15
4